Create locations table for Mangrove Atlas

@author Alicia A. Arenzana (Vizzuality) adapted from  (GEE script)[]
Prepares featureCollection of geometries, and adds properties (length_coastline, area, perimeter)
Notes:
- WDPA protected areas are only 'Ramsar' sites and NOT proposed
Gotchas: 
- Only selected properties are selected for export!
- Only export as geosjon
- geometries with holes cause issues; polygon list > 1

In [57]:
import uuid
from typing import Union, List
from random import randint
import ee
import json
import geopandas as gpd
# Imports the Google Cloud client library
from google.cloud import storage

In [33]:
# Trigger the authentication flow.
ee.Authenticate()
ee.Initialize()


Successfully saved authorization token.


In [42]:
uuid_camerun = uuid.uuid5(uuid.NAMESPACE_OID, '{"type":"Camerun"}')
print(uuid_camerun)

4b0faded-7816-5599-b8d5-1b275b1d7650


In [43]:
uuid_camerun_t = uuid.uuid5(uuid.NAMESPACE_OID, '{"type":"Camerun"}')
print(uuid_camerun)
print(uuid_camerun_t)

4b0faded-7816-5599-b8d5-1b275b1d7650
4b0faded-7816-5599-b8d5-1b275b1d7650


In [70]:
# LIST OF ISO WITH MANGROVES
MG_ISO_LIST = ["TZA","SEN","CIV","CMR","COM","CRI","CUB","CYM","DJI","ECU","EGY","ERI","FJI","FSM",
"GAB","SLE","SLV","SYC","TCA","THA","TLS","TON","TWN","USA","GHA","GIN","GMB","GNB","GNQ","GRD","GTM",
"GUF","HND","IDN","IND","IRN","JAM","JPN","KHM","KNA","LBR","LCA","LKA","MAF","MDG","MEX","MMR","MOZ",
"MUS","MYT","NGA","NZL","OMN","PAK","PAN","PHL","PLW","PNG","QAT","SAU","VCT","VEN","VGB","VNM","WSM",
"YEM","ZAF","-","ARE","ATG","BEN","BES","BGD","BHR","BHS","BLZ","BRA","BRN","CHN","GLP","GUY","KEN",
"MYS","NCL","NIC","PER","PRI","SDN","SGP","SLB","SOM","SUR","TTO","VUT","HTI","MTQ","VIR","AGO","AUS",
"COD","COL","DOM"]
    

# Coastline data
# aoi's rufiji and saloum 
# * map the properties adding {'type': 'aoi', 'name': 'Rufiji Delta', 'iso': 'TZA', 'dashboardId':""}
# EEZ data
# * filter by iso with mangroves.
#*  map properties adding {'type': 'country', 'name': name, 'iso': iso, 'dashboardId':""}
# wdpa data
# * filter by iso with mangroves.
# * filter by status excluding proposed.
# * filter by designation including Ramsar.
# * map properties adding {'type': 'wdpa','name': name,'iso': iso,'iucn_cat': iucn_cat,'dashboardId':"", 'designation_eng': designation_eng}



In [ ]:
# GC storage blob management.

def download_blob(bucket_name: str, source_blob_name: str, destination_file_name: str) -> str:
    """Downloads a blob from the bucket.
    
    args:
        bucket_name: The bucket to download from. "your-bucket-name"
        source_blob_name: The name of the blob to download. "storage-object-name"
        destination_file_name: The name of the file to download to "local/path/to/file".

    returns:
        The path to the downloaded file.
    """

    storage_client = storage.Client()

    bucket = storage_client.bucket(bucket_name)

    # Construct a client side representation of a blob.
    # Note `Bucket.blob` differs from `Bucket.get_blob` as it doesn't retrieve
    # any content from Google Cloud Storage. As we don't need additional data,
    # using `Bucket.blob` is preferred here.
    blob = bucket.blob(source_blob_name)
    blob.download_to_filename(destination_file_name)

    print(
        "Downloaded storage object {} from bucket {} to local file {}.".format(
            source_blob_name, bucket_name, destination_file_name
        )
    )
    return destination_file_name

def upload_blob(bucket_name: str, source_file_name: str, destination_blob_name: str) -> str:
    """Uploads a file to the bucket.
    
    Args:
        bucket_name: The bucket to upload to. "your-bucket-name"
        source_file_name: The path to the file to upload. "local/path/to/file"
        destination_blob_name: The name of the blob to upload to. "storage-object-name"
    
    Returns:
        The public url of the uploaded file.
    
    """

    storage_client = storage.Client()
    bucket = storage_client.bucket(bucket_name)
    blob = bucket.blob(destination_blob_name)

    blob.upload_from_filename(source_file_name)

    print(
        "File {} uploaded to {}.".format(
            source_file_name, destination_blob_name
        )
    )
    return destination_blob_name


In [55]:
class AreaTypes():
    wdpa = 'wdpa'
    eez = 'eez'
    aoi = 'aoi'
    country = 'country'
    coastline = 'coastline'

In [85]:
def aoi_data(aoi_sources: List[str], filter: Union[None, dict] = None) -> ee.FeatureCollection:
    """
    Create an area of interest from the aoi_sources.
    """
    base_path = 'projects/global-mangrove-watch/boundaries/'

    aoi_data = ee.FeatureCollection([])
    new_aoi_data = None
    
    for aoi in aoi_sources:
        if base_path in aoi:
            asset_name = aoi.split(base_path)[-1].split('_')
            
            ## This is because the data uploaded in GEE does lack that information
            new_aoi_data = ee.FeatureCollection(aoi).map(
                lambda f: f.set({'type': AreaTypes.aoi, 
                    'name': f'{asset_name[1].capitalize()} Delta', 
                    'iso': asset_name[2], 
                    'dashboardId':""})
                )
            
            aoi_data.merge(new_aoi_data)
    
    return aoi_data

def coastline_data(filter: Union[None, dict] = None):
    """
    load the coastline data.
    """
    return ee.FeatureCollection('projects/global-mangrove-watch/physical-environment/ne_10m_coastline')

def eez_data(filter: Union[None, dict] = MG_ISO_LIST):
    '''
    
    '''
    eez = ee.FeatureCollection('projects/global-mangrove-watch/boundaries/EEZ_land_union_v3_202003')
    
    if filter: 
        eez = eez.filter(ee.Filter.inList('ISO_SOV1', filter))

    iso_list = ee.List(eez.aggregate_array('ISO_SOV1')).distinct()
    
    eez = eez.map(lambda f: f.set(
                {'type': AreaTypes.country, 
                'name': f.get('SOVEREIGN1'), 
                'iso': f.get('ISO_SOV1'), 
                'dashboardId':""}
                )
            )
    def eez_merge(iso:str) -> ee.FeatureCollection:
    
        sel = eez.filter(ee.Filter.eq('ISO_SOV1', iso))
        return ee.Feature(sel.geometry().dissolve(), {}
        ).copyProperties(sel.select(['type', 'name', 'iso', 'dashboardId']).first())
    # agrregate geometries by iso
    return iso_list.map(eez_merge)


def wdpa_data(filter: Union[None, dict] = None):
    '''
    
    '''
    return ee.FeatureCollection('projects/global-mangrove-watch/boundaries/wdpa_polygons_latest_cleaned').filter(
        ee.Filter.neq('STATUS', 'Proposed')).filter(
            ee.Filter.stringContains('DESIG_ENG','Ramsar')).filter(
                ee.Filter.inList('ISO3', MG_ISO_LIST)).map(
                    lambda f: f.set({'type': AreaTypes.wdpa,
                    'name': f.get('NAME'),
                    'iso': f.get('ISO3'),
                    'iucn_cat': f.get('IUCN_CAT'),
                    'dashboardId':"",
                    'designation_eng': f.get('DESIG_ENG')})
                )

In [87]:
eez_data().getInfo()

[{'type': 'Feature',
  'geometry': {'type': 'Polygon',
   'coordinates': [[[8.326078093798072, 4.069326598481361],
     [8.330220584848085, 4.071016551317995],
     [8.364693922415562, 4.079471010848074],
     [8.380363161297467, 4.083123035224028],
     [8.417623432379012, 4.091831665201625],
     [8.455235907943512, 4.098752215662926],
     [8.515505166888046, 4.1098776465045495],
     [8.522782382087438, 4.111099457894047],
     [8.523263946579478, 4.111188626683498],
     [8.540899714711626, 4.114492826000583],
     [8.584616754645587, 4.123406569015298],
     [8.61261544140531, 4.115892965711333],
     [8.628226741285005, 4.111045907273467],
     [8.636850695451203, 4.10608736775651],
     [8.654914502765136, 4.0951358650565926],
     [8.672304978393184, 4.083992591606835],
     [8.689017709748214, 4.072661984876223],
     [8.705052582915386, 4.061148583783917],
     [8.720414207174198, 4.049443449708351],
     [8.735102509938228, 4.037555514100721],
     [8.744172297999667, 4.029

In [ ]:


def create_locations(overwrite: bool = False, new_locations: Union[None, dict] = None):
    """
    Create locations from the data.
    """
   
    
    
    if overwrite:
        # trigger the full process
        pass
    else:
        # trigger the incremental process
        pass





def wdpa_data(filter: Union[None, dict] = None):
    '''
    
    '''
    return ee.FeatureCollection('projects/global-mangrove-watch/boundaries/wdpa_polygons_latest_cleaned').filter(
        ee.Filter.neq('STATUS', 'Proposed')).filter(
            ee.Filter.stringContains('DESIG_ENG','Ramsar')).filter(
                ee.Filter.inList('ISO3', MG_ISO_LIST)).map(
                    lambda f: f.set({'type': AreaTypes.wdpa,
                    'name': f.get('NAME'),
                    'iso': f.get('ISO3'),
                    'iucn_cat': f.get('IUCN_CAT'),
                    'dashboardId':"",
                    'designation_eng': f.get('DESIG_ENG')})
                )




def merge_by_iso():
    pass

def merge_locations():
    pass

def calculate_summaries():
    pass
